# Cohort Building

**Example use case:** 

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" alt="alt_text" align="left"
	width="150" height="150" />
Julia is an oncologist that specializes in female reproductive health. As part of her research, she is interested in  using existing data on uterine cancers. If possible, she would like to see multiple datatypes (gross imaging, genomic data, proteomic data, histology) that come from the same patient, so she can look for shared phenotypes to test for their potential as early diagnostics. Julia heard that the Cancer Data Aggregator has made it easy to search across multiple datasets created by NCI, and so has decided to start her search there.



## Getting Started

The CDA provides a custom python tool for searching CDA data. [`Q`](usage/#q) (short for Query) offers several ways to search and filter data, and several input modes:

---
- **<a href="../../QuickStart/usage/#q">Q.()</a>** builds a query that can be used by `run()` or `count()`
- **<a href="../../QuickStart/usage/#qrun">Q.run()</a>** returns data for the specified search 
- **<a href="../../QuickStart/usage/#qcount">Q.count()</a>** returns summary information (counts) data that fit the specified search
- **<a href="../../QuickStart/usage/#columns">columns()</a>** returns entity field names
- **<a href="../../QuickStart/usage/#unique_terms">unique_terms()</a>** returns entity field contents

---

Before Julia does any work, she needs to import these functions cdapython.
She'll also need to import [pandas](https://pandas.pydata.org/) to work with dataframes and itables to display them nicely. The `opt.` settings are pre-configuring how itables should display her tables, with scrolling and paging enabled.

In [30]:
from cdapython import (
    Q, columns, unique_terms, set_default_project_dataset, set_host_url, 
    set_table_version, get_host_url, get_default_project_dataset, get_table_version 
)
import numpy as np
import pandas as pd
from itables import init_notebook_mode, show
init_notebook_mode(all_interactive=True)
import itables.options as opt
opt.maxBytes=0
opt.scrollX="200px"
opt.scrollCollapse=True
opt.paging=True
opt.maxColumns=0

set_default_project_dataset("gdc-bq-sample.dev")
set_host_url("http://35.192.60.10:8080/")
set_table_version("all_merged_subjects_v3_2_final")

print(get_host_url())
print(get_default_project_dataset())
print(get_table_version())
print(Q.get_version())

<IPython.core.display.Javascript object>

http://35.192.60.10:8080/

gdc-bq-sample.dev

all_merged_subjects_v3_2_final

2023.4.18

<div class="cdanote" style="background-color:#b3e5d5;color:black;padding:20px;">
    
CDA data comes from three sources:
<ul>
<li><b>The <a href="https://proteomic.datacommons.cancer.gov/pdc/"> Proteomic Data Commons</a> (PDC)</b></li>
<li><b>The <a href="https://gdc.cancer.gov/">Genomic Data Commons</a> (GDC)</b></li>
<li><b>The <a href="https://datacommons.cancer.gov/repository/imaging-data-commons">Imaging Data Commons</a> (IDC)</b></li>
</ul> 
    
The CDA makes this data searchable in four main endpoints:

<ul>
<li><b>subject:</b> A patient entity captures the study-independent metadata for research subjects. Human research subjects are usually not traceable to a particular person to protect the subjects privacy.</li>
<li><b>researchsubject:</b> A research subject is the entity of interest in a specific research study or project, typically a human being or an animal, but can also be a device, group of humans or animals, or a tissue sample. Human research subjects are usually not traceable to a particular person to protect the subjects privacy. This entity plays the role of the case_id in existing data. A subject who participates in 3 studies will have 3 researchsubject IDs.</li>
<li><b>specimen:</b> Any material taken as a sample from a biological entity (living or dead), or from a physical object or the environment. Specimens are usually collected as an example of their kind, often for use in some investigation.</li>
<li><b>mutation:</b> Molecular data about specific mutations, currently limited to the TCGA-READ project from GDC.</li>
</ul>
one endpoint that can be added to the subject, researchsubject, or specimen to get the relevant files:    
<ul>
<li><b>file:</b> A unit of data about subjects, researchsubjects, specimens, or their associated information.</li>
</ul>
and two endpoints that offer deeper information about data in the researchsubject endpoint:
<ul>
<li><b>diagnosis:</b> A collection of characteristics that describe an abnormal condition of the body as assessed at a point in time. May be used to capture information about neoplastic and non-neoplastic conditions.</li>
<li><b>treatment:</b> Represent medication administration or other treatment types.</li>
</ul>
</div>


Any metadata field can be searched from any endpoint, the only difference between search types is what type of data is returned by default. This means that you can think of the CDA as a really, really enormous spreadsheet full of data. To search this enormous spreadsheet, you'd want select columns, and then filter rows.
</div>


## Finding Search Terms

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
   
   Accordingly, to see what search fields are available, Julia starts by using the command `columns`:

In [31]:
columns().to_dataframe()

fieldName   endpoint  \
0                  ALLELE_NUM   mutation   
1                    fileName   mutation   
2                        PICK   mutation   
3     days_to_treatment_start  treatment   
4                     Feature   mutation   
..                        ...        ...   
175  Tumor_Validation_Allele1   mutation   
176               Exon_Number   mutation   
177           normal_bam_uuid   mutation   
178                 MINIMISED   mutation   
179                     HGVSc   mutation   

                                           description     type      mode  
0    Allele number from input; 0 is reference, 1 is...   STRING  NULLABLE  
1      |-delimited list of name of underlying MAF file   STRING  NULLABLE  
2    Indicates if this block of consequence data wa...   STRING  NULLABLE  
3        The timepoint at which the treatment started.  INTEGER  NULLABLE  
4    Stable Ensembl ID of feature (transcript, regu...   STRING  NULLABLE  
..                                                 ...      ...       ...  
175  Secondary data from orthogonal technology. Tum...   STRING  NULLABLE  
176              The exon number (out of total number)   STRING  NULLABLE  
177  Unique GDC identifier for the underlying norma...   STRING  NULLABLE  
178  Alleles in this variant have been converted to...   STRING  NULLABLE  
179  The coding sequence of the variant in HGVS rec...   STRING  NULLABLE  

[180 rows x 5 columns]

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
   
There are a lot of columns in the CDA data, but Julia is most interested in diagnosis data, so she searches the description column for "diagnosis":

In [32]:
columns().to_dataframe(search_fields=["description", "fieldName"],search_value="diagnosis")

fieldName         endpoint  \
0                 age_at_diagnosis        diagnosis   
1      primary_diagnosis_condition  researchsubject   
2                     diagnosis_id        diagnosis   
3           primary_diagnosis_site  researchsubject   
4  diagnosis_identifier_field_name        diagnosis   
5      diagnosis_identifier_system        diagnosis   
6              method_of_diagnosis        diagnosis   
7       diagnosis_identifier_value        diagnosis   
8                primary_diagnosis        diagnosis   

                                         description     type      mode  
0  The age in days of the individual at the time ...  INTEGER  NULLABLE  
1  The text term used to describe the type of mal...   STRING  NULLABLE  
2  The 'logical' identifier of the entity in the ...   STRING  REQUIRED  
3  The text term used to describe the primary sit...   STRING  NULLABLE  
4  The name of the data object in the originating...   STRING  NULLABLE  
5  The system or namespace that defines the ident...   STRING  NULLABLE  
6  The method used to confirm the subjects malign...   STRING  NULLABLE  
7  The value of the identifier, as defined by the...   STRING  NULLABLE  
8  The diagnosis instance that qualified a subjec...   STRING  NULLABLE

<div class="cdanote" style="background-color:#b3e5d5;color:black;padding:20px;">

To search the CDA, a user also needs to know what search terms are available. Each column will contain a huge amount of data, so retrieving all of the rows would be overwhelming. Instead, the CDA has a `unique_terms()` function that will return all of the unique values that populate the requested column. Like `columns`, `unique_terms` defaults to giving us an overview of the results, and can be filtered.
    
</div>

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Since Julia is interested specifically in uterine cancers, she looks for columns that appear to have anatomical data, and then uses the `unique_terms` function to see what data is available for 'treatment_anatomic_site' and 'primary_diagnosis_site' to see if 'uterine' appears, she uses the `show_counts` flag so she can also see how much data is associated with each term:

In [33]:
unique_terms("treatment_anatomic_site", show_counts = True).to_dataframe()

treatment_anatomic_site  Count
0                      None  33351
1                     Brain      5
2                    Cervix     87
3  Head - Face Or Neck, Nos      1
4  Lymph Node(s) Paraaortic     34
5                     Other      3
6                    Pelvis    102
7                     Spine      2
8                   Unknown    125

In [34]:
unique_terms("primary_diagnosis_site", show_counts = True).to_dataframe()

primary_diagnosis_site  Count
0                                                None    833
1                                             Abdomen    112
2   Abdomen, Arm, Bladder, Chest, Head-Neck, Kidne...     89
3                                Abdomen, Mediastinum    176
4                                     Abdomen, Pelvis    230
..                                                ...    ...
94                                             Uterus    867
95                                        Uterus, NOS   2349
96                                             Vagina     72
97                                            Various    458
98                                              Vulva     10

[99 rows x 2 columns]

<div class="cdanote" style="background-color:#b3e5d5;color:black;padding:20px;">
    
CDA makes multiple datasets searchable from a common interface, but does not harmonize the data. This means that researchers should review all the terms in a column, and not just choose the first one that fits, as there may be other similar terms available as well.
    
</div>

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Julia sees that "treatment_anatomic_site" does not have 'Uterine', but does have 'Cervix'. She also notes that both 'Uterus' and 'Uterus, NOS' are listed in the "primary_diagnosis_site" results. As she was initially looking for "uterine", Julia decides to expand her search a bit to account for variable naming schemes. So, she runs a fuzzy match filter on the "ResearchSubject.primary_diagnosis_site" for 'uter' as that should cover all variants:

In [36]:
unique_terms("primary_diagnosis_site").to_list(filters="uter")

['Abdomen, Arm, Bladder, Chest, Head-Neck, Kidney, Leg, Retroperitoneum, Stomach, Uterus',
 'Cervix uteri',
 'Corpus uteri',
 'Uterus',
 'Uterus, NOS']

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Just to be sure, Julia also searches for any other instances of "cervix":

In [37]:
unique_terms("primary_diagnosis_site").to_list(filters="cerv")

['Cervix', 'Cervix uteri']

## Building a Query

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
With all her likely terms found, Julia begins to create a search that will get data for all of her terms. She does this by writing a series of `Q` statements that define what rows should be returned from each column. For the "treatment_anatomic_site", only one term is of interest, so she uses the `=` operator to get only exact matches:

In [38]:
Tsite = Q('treatment_anatomic_site = "Cervix"')

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
However, for "primary_diagnosis_site", Julia has several terms she wants to search with. Luckily, `Q` also can run fuzzy searches. It can also search more than one term at a time, so Julia writes one big `Q` statement to grab everything that is either 'uter' or 'cerv':

In [39]:
Dsite = Q('primary_diagnosis_site = "%uter%" OR primary_diagnosis_site = "%cerv%"')

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Finally, Julia adds her two queries together into one large one:

In [40]:
ALLDATA = Tsite.OR(Dsite)

## Looking at Summary Data

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Now that Julia has a query, she can use it to look for data in any of the CDA endpoints. She starts by getting an overall summary of what data is available using `count`:

In [41]:
ALLDATA.count.run()

Getting results from database

Total execution time: 0
                            min 3.596 sec 3596 ms

specimen_count : 47022

treatment_count : 3049

diagnosis_count : 4057

mutation_count : 0

researchsubject_count : 5330

subject_count : 3857

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
It seems there's a lot of data that might work for Julias study! Since she is interested in the beginings of cancer, she decides to start by looking at  the researchsubject information, since that is where most of the diagnosis information is. She again gets a summary using `count`:

In [42]:
ALLDATA.researchsubject.count.run()

Getting results from database

Total execution time: 0
                            min 3.657 sec 3657 ms

files : 368012

total : 5330

primary_diagnosis_condition 
 count 
 
 
 
 
 Squamous Cell Neoplasms 
 609 
 
 
 Adenomas and Adenocarcinomas 
 1825 
 
 
 Cystic, Mucinous and Serous Neoplasms 
 490 
 
 
 Complex Epithelial Neoplasms 
 27 
 
 
 Uterine Corpus Endometrial Carcinoma 
 872 
 
 
 Not Reported 
 12 
 
 
 Complex Mixed and Stromal Neoplasms 
 322 
 
 
 Sarcomas 
 89 
 
 
 Corpus Endometrial Carcinoma 
 250 
 
 
 Cervical Squamous Cell Carcinoma and Endocervical Adenocarcinoma 
 307 
 
 
 Uterine Carcinosarcoma 
 57 
 
 
 Myomatous Neoplasms 
 190 
 
 
 None 
 1 
 
 
 Epithelial Neoplasms, NOS 
 230 
 
 
 Soft Tissue Tumors and Sarcomas, NOS 
 14 
 
 
 Trophoblastic neoplasms 
 13 
 
 
 Neoplasms, NOS 
 16 
 
 
 Mesonephromas 
 5 
 
 
 Neuroepitheliomatous Neoplasms 
 1 
 
 
 

 
 
 
 primary_diagnosis_site 
 count 
 
 
 
 
 Cervix uteri 
 917 
 
 
 Uterus, NOS 
 2349 
 
 
 Corpus uteri 
 801 
 
 
 Uterus 
 867 
 
 
 Cervix 
 307 
 
 
 Abdomen, Arm, Bladder, Chest, Head-Neck, Kidney, Leg, Retroperitoneum, Stomach, Uterus 
 89 
 
 
 

 
 
 
 researchsubject_identifier_system 
 count 
 
 
 
 
 GDC 
 3755 
 
 
 PDC 
 312 
 
 
 IDC 
 1263

## Refining Queries

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Browsing the primary_diagnosis_condition data, Julia notices that there are a large number of research subjects that are Adenomas and Adenocarcinomas. Since Julia wants to look for common phenotypes in early cancers, she decides it might be easier to exclude the endocrine related data, as they might have different mechanisms. So she adds a new filter to her query:

In [43]:
Noadeno = Q('primary_diagnosis_condition != "Adenomas and Adenocarcinomas"')

NoAdenoData = ALLDATA.AND(Noadeno)

NoAdenoData.researchsubject.count.run()

Getting results from database

Total execution time: 0
                            min 3.766 sec 3766 ms

files : 364646

total : 3505

primary_diagnosis_condition 
 count 
 
 
 
 
 Squamous Cell Neoplasms 
 609 
 
 
 Myomatous Neoplasms 
 190 
 
 
 Uterine Corpus Endometrial Carcinoma 
 872 
 
 
 Cystic, Mucinous and Serous Neoplasms 
 490 
 
 
 Complex Mixed and Stromal Neoplasms 
 322 
 
 
 Sarcomas 
 89 
 
 
 Corpus Endometrial Carcinoma 
 250 
 
 
 Cervical Squamous Cell Carcinoma and Endocervical Adenocarcinoma 
 307 
 
 
 Uterine Carcinosarcoma 
 57 
 
 
 Not Reported 
 12 
 
 
 Epithelial Neoplasms, NOS 
 230 
 
 
 Neoplasms, NOS 
 16 
 
 
 Trophoblastic neoplasms 
 13 
 
 
 Complex Epithelial Neoplasms 
 27 
 
 
 Soft Tissue Tumors and Sarcomas, NOS 
 14 
 
 
 None 
 1 
 
 
 Mesonephromas 
 5 
 
 
 Neuroepitheliomatous Neoplasms 
 1 
 
 
 

 
 
 
 primary_diagnosis_site 
 count 
 
 
 
 
 Cervix uteri 
 688 
 
 
 Uterus, NOS 
 1171 
 
 
 Corpus uteri 
 383 
 
 
 Uterus 
 867 
 
 
 Cervix 
 307 
 
 
 Abdomen, Arm, Bladder, Chest, Head-Neck, Kidney, Leg, Retroperitoneum, Stomach, Uterus 
 89 
 
 
 

 
 
 
 researchsubject_identifier_system 
 count 
 
 
 
 
 GDC 
 1930 
 
 
 PDC 
 312 
 
 
 IDC 
 1263

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
She then previews the actual metadata for researchsubject, subject, and file, to make sure that they have all the information she will need for her work. Since she's mostly interested in looking at the kinds of data available from each endpoint:

In [44]:
NoAdenoData.researchsubject.run().to_dataframe() # view the dataframe

Getting results from database

Total execution time: 0
                            min 3.783 sec 3783 ms

researchsubject_id  \
0   GENIE-NKI.GENIE-NKI-C0BP   
1   GENIE-NKI.GENIE-NKI-3OX3   
2   GENIE-NKI.GENIE-NKI-3GI3   
3   GENIE-NKI.GENIE-NKI-AGW0   
4   GENIE-NKI.GENIE-NKI-LVFM   
..                       ...   
95              FM-AD.AD5188   
96              FM-AD.AD5838   
97              FM-AD.AD8976   
98               FM-AD.AD552   
99             FM-AD.AD16769   

                           researchsubject_identifier  \
0   [{'system': 'GDC', 'field_name': 'case.case_id...   
1   [{'system': 'GDC', 'field_name': 'case.case_id...   
2   [{'system': 'GDC', 'field_name': 'case.case_id...   
3   [{'system': 'GDC', 'field_name': 'case.case_id...   
4   [{'system': 'GDC', 'field_name': 'case.case_id...   
..                                                ...   
95  [{'system': 'GDC', 'field_name': 'case.case_id...   
96  [{'system': 'GDC', 'field_name': 'case.case_id...   
97  [{'system': 'GDC', 'field_name': 'case.case_id...   
98  [{'system': 'GDC', 'field_name': 'case.case_id...   
99  [{'system': 'GDC', 'field_name': 'case.case_id...   

   member_of_research_project            primary_diagnosis_condition  \
0                   GENIE-NKI    Complex Mixed and Stromal Neoplasms   
1                   GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
2                   GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
3                   GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
4                   GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
..                        ...                                    ...   
95                      FM-AD                Squamous Cell Neoplasms   
96                      FM-AD                Squamous Cell Neoplasms   
97                      FM-AD                Squamous Cell Neoplasms   
98                      FM-AD                Squamous Cell Neoplasms   
99                      FM-AD    Complex Mixed and Stromal Neoplasms   

   primary_diagnosis_site            subject_id  
0             Uterus, NOS  GENIE.GENIE-NKI-C0BP  
1            Cervix uteri  GENIE.GENIE-NKI-3OX3  
2            Cervix uteri  GENIE.GENIE-NKI-3GI3  
3            Cervix uteri  GENIE.GENIE-NKI-AGW0  
4            Cervix uteri  GENIE.GENIE-NKI-LVFM  
..                    ...                   ...  
95           Cervix uteri             FM.AD5188  
96           Cervix uteri             FM.AD5838  
97           Cervix uteri             FM.AD8976  
98           Cervix uteri              FM.AD552  
99            Uterus, NOS            FM.AD16769  

[100 rows x 6 columns]

---

<div class="cdadefine" style="background-color:#add9e5;color:black;padding:20px;">

<h3>ResearchSubject Field Definitions</h3>

<i>A research subject is the entity of interest in a specific research study or project, typically a human being or an animal, but can also be a device, group of humans or animals, or a tissue sample. Human research subjects are usually not traceable to a particular person to protect the subjects privacy. This entity plays the role of the case_id in existing data. An individual who participates in 3 studies will have 3 researchsubject IDs</i>
    
<ul>
<li><b>id:</b> The 'logical' identifier of the entity in the system of record, e.g. a UUID. This 'id' is unique within a given system. The identified entity may have a different 'id' in a different system. For CDA, this is case_id.</li>
<li><b>identifier:</b> A 'business' identifier for the entity, typically as provided by an external system or authority, that persists across implementing systems (i.e. a 'logical' identifier). Uses a specialized, complex 'Identifier' data type to capture information about the source of the business identifier - or a URI expressed as a string to an existing entity.</li>
<li><b>identifier.system:</b> The system or namespace that defines the identifier.</li>
<li><b>identifier.value:</b> The value of the identifier, as defined by the system.</li>
<li><b>member_of_research_project:</b> A reference to the Study(s) of which this ResearchSubject is a member.</li>
<li><b>primary_diagnosis_condition:</b> The text term used to describe the type of malignant disease, as categorized by the World Health Organization's (WHO) <a href="https://www.who.int/standards/classifications/other-classifications/international-classification-of-diseases-for-oncology">International Classification of Diseases for Oncology</a> (ICD-O). This attribute represents the disease that qualified the subject for inclusion on the ResearchProject.</li>
<li><b>primary_diagnosis_site:</b> The text term used to describe the primary site of disease, as categorized by the World Health Organization's (WHO) <a href="https://www.who.int/standards/classifications/other-classifications/international-classification-of-diseases-for-oncology">International Classification of Diseases for Oncology</a> (ICD-O). This categorization groups cases into general categories. This attribute represents the primary site of disease that qualified the subject for inclusion on the ResearchProject.</li>
<li><b>subject_id:</b> The 'logical' identifier of the entity in the system of record, e.g. a UUID. This 'id' is unique within a given system. The identified entity may have a different 'id' in a different system. Can be joined to the `id` field from subject results</li>
</ul>  

</div>
    
---

In [45]:
NoAdenoData.subject.run().to_dataframe() # view the dataframe

Getting results from database

Total execution time: 0
                            min 3.764 sec 3764 ms

subject_id  \
0    CGCI.HTMCP-03-06-02393   
1           CPTAC.C3L-01599   
2           CPTAC.C3L-03264   
3           CPTAC.C3N-00847   
4           CPTAC.C3N-01344   
..                      ...   
95  GENIE.GENIE-DFCI-003828   
96  GENIE.GENIE-DFCI-006811   
97  GENIE.GENIE-DFCI-023745   
98  GENIE.GENIE-DFCI-035037   
99  GENIE.GENIE-DFCI-037251   

                                   subject_identifier       species     sex  \
0   [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
1   [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
2   [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
3   [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
4   [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
..                                                ...           ...     ...   
95  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
96  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
97  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
98  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
99  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   

                         race               ethnicity  days_to_birth  \
0   black or african american  not hispanic or latino       -12315.0   
1                       white  not hispanic or latino       -24089.0   
2                       white  not hispanic or latino       -26833.0   
3                       other            not reported       -23757.0   
4                       white            not reported       -29270.0   
..                        ...                     ...            ...   
95  black or african american  not hispanic or latino       -14610.0   
96                      white  not hispanic or latino       -26298.0   
97                      white  not hispanic or latino       -26298.0   
98                      white  not hispanic or latino       -24106.0   
99                      white  not hispanic or latino       -16071.0   

                           subject_associated_project  vital_status  \
0                                     [CGCI-HTMCP-CC]          Dead   
1                               [CPTAC-3, cptac_ucec]         Alive   
2                               [CPTAC-3, cptac_ucec]         Alive   
3   [CPTAC-3, PDC000125, PDC000126, PDC000226, cpt...         Alive   
4                               [CPTAC-3, cptac_ucec]          Dead   
..                                                ...           ...   
95                                       [GENIE-DFCI]  Not Reported   
96                                       [GENIE-DFCI]  Not Reported   
97                                       [GENIE-DFCI]  Not Reported   
98                                       [GENIE-DFCI]  Not Reported   
99                                       [GENIE-DFCI]  Not Reported   

    days_to_death cause_of_death  
0           648.0   Not Reported  
1             NaN           None  
2             NaN           None  
3             NaN           None  
4          1359.0           None  
..            ...            ...  
95            NaN           None  
96            NaN           None  
97            NaN           None  
98            NaN           None  
99            NaN           None  

[100 rows x 11 columns]

---

<div class="cdadefine" style="background-color:#add9e5;color:black;padding:20px;">

<h3>Subject Field Definitions</h3>

<i>A patient entity captures the study-independent metadata for research subjects. Human research subjects are usually not traceable to a particular person to protect the subjects privacy.</i>

    
<ul>
<li><b>id:</b> The 'logical' identifier of the entity in the system of record, e.g. a UUID. This 'id' is unique within a given system. The identified entity may have a different 'id' in a different system.",STRING</li>
<li><b>identifier:</b> A 'business' identifier for the entity, typically as provided by an external system or authority, that persists across implementing systems (i.e. a 'logical' identifier). Uses a specialized, complex 'Identifier' data type to capture information about the source of the business identifier - or a URI expressed as a string to an existing entity.</li>
<li><b>identifier.system:</b> The system or namespace that defines the identifier.</li>
<li><b>identifier.value:</b> The value of the identifier, as defined by the system.</li>
<li><b>species:</b> The taxonomic group (e.g. species) of the patient. For MVP, since taxonomy vocabulary is consistent between GDC and PDC, using text. Ultimately, this will be a term returned by the vocabulary service.</li>
<li><b>sex:</b> The biologic character or quality that distinguishes male and female from one another as expressed by analysis of the person's gonadal, morphologic (internal and external), chromosomal, and hormonal characteristics.</li>
<li><b>race:</b> An arbitrary classification of a taxonomic group that is a division of a species. It usually arises as a consequence of geographical isolation within a species and is characterized by shared heredity, physical attributes and behavior, and in the case of humans, by common history, nationality, or geographic distribution. The provided values are based on the categories defined by the U.S. Office of Management and Business and used by the U.S. Census Bureau.</li>
<li><b>ethnicity:</b> An individual's self-described social and cultural grouping, specifically whether an individual describes themselves as Hispanic or Latino. The provided values are based on the categories defined by the U.S. Office of Management and Business and used by the U.S. Census Bureau.</li>
<li><b>days_to_birth:</b> Number of days between the date used for index and the date from a person's date of birth represented as a calculated negative number of days.</li>
<li><b>subject_associated_project:</b> The list of Projects associated with the Subject.</li>
<li><b>vital_status:</b> Coded value indicating the state or condition of being living or deceased; also includes the case where the vital status is unknown.</li>
<li><b>days_to_death:</b> Number of days between the date used for index and the date from a person's date of death represented as a calculated number of days.</li>
<li><b>cause_of_death:</b> Coded value indicating the circumstance or condition that results in the death of the subject.</li>
</ul>  

</div>
    
---

In [46]:
NoAdenoData.subject.file.run()# view the dataframe

Getting results from database

Total execution time: 0
                            min 3.968 sec 3968 ms


            
            Offset: 0
            Count: 100
            Total Row Count: 398444
            More pages: True
            


---

<div class="cdadefine" style="background-color:#add9e5;color:black;padding:20px;">

<h3>File Field Definitions</h3>

<i>A file is an information-bearing electronic object that contains a physical embodiment of some information using a particular character encoding.</i>

    
<ul>
  <li><b>id:</b> The 'logical' identifier of the entity in the system of record, e.g. a UUID. This 'id' is unique within a given system. The identified entity may have a different 'id' in a different system.</li>
<li><b>identifier:</b> A 'business' identifier for the entity, typically as provided by an external system or authority, that persists across implementing systems (i.e. a 'logical' identifier). Uses a specialized, complex 'Identifier' data type to capture information about the source of the business identifier - or a URI expressed as a string to an existing entity.</li>
<li><b>identifier.system:</b> The system or namespace that defines the identifier.</li>
<li><b>identifier.value:</b> The value of the identifier, as defined by the system.</li>
  <li><b>label:</b> Short name or abbreviation for dataset. Maps to rdfs:label.</li>
  <li><b>data_catagory:</b> Broad categorization of the contents of the data file.</li>
  <li><b>data_type:</b> Specific content type of the data file.</li>
  <li><b>file_format:</b> Format of the data files.</li>
  <li><b>associated_project:</b> A reference to the Project(s) of which this ResearchSubject is a member. The associated_project may be embedded using the ref definition or may be a reference to the id for the Project - or a URI expressed as a string to an existing entity.</li>
  <li><b>drs_uri:</b> A string of characters used to identify a resource on the Data Repo Service(DRS). Can be used to retrieve this specific file from a server.</li>
  <li><b>byte_size:</b> Size of the file in bytes. Maps to dcat:byteSize.</li>
  <li><b>checksum:</b> The md5 value for the file. A digit representing the sum of the correct digits in a piece of stored or transmitted digital data, against which later comparisons can be made to detect errors in the data.</li>
  <li><b>data_modality:</b> Data modality describes the biological nature of the information gathered as the result of an Activity, independent of the technology or methods used to produce the information. Always one of "Genomic", "Proteomic", or "Imaging".</li>
  <li><b>imaging_modality:</b> An imaging modality describes the imaging equipment and/or method used to acquire certain structural or functional information about the body. These include but are not limited to computed tomography (CT) and magnetic resonance imaging (MRI). Taken from the DICOM standard.</li>
  <li><b>dbgap_accession_number:</b> The dbgap accession number for the project.</li>
</ul>  

</div>
    
---


## Working with Results (pagination)

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Finally, Julia wants to save these results to use for the future. Since the preview dataframes only show the first 100 results of each search, she uses the `paginator` function to get all the data from the subject and researchsubject endpoints into their own dataframes:

In [47]:
researchsubs = NoAdenoData.researchsubject.run()
rsdf = researchsubs.get_all().to_dataframe()

Getting results from database

Total execution time: 0
                            min 4.189 sec 4189 ms

In [48]:
subs = NoAdenoData.subject.run()
subsdf = subs.get_all().to_dataframe()

Getting results from database

Total execution time: 0
                            min 3.593 sec 3593 ms

In [49]:
rsdf # view the researchsubject dataframe

researchsubject_id  \
0            GENIE-NKI.GENIE-NKI-C0BP   
1            GENIE-NKI.GENIE-NKI-3OX3   
2            GENIE-NKI.GENIE-NKI-3GI3   
3            GENIE-NKI.GENIE-NKI-AGW0   
4            GENIE-NKI.GENIE-NKI-LVFM   
...                               ...   
3500  CGCI-HTMCP-CC.HTMCP-03-06-02327   
3501  CGCI-HTMCP-CC.HTMCP-03-06-02213   
3502  CGCI-HTMCP-CC.HTMCP-03-06-02321   
3503  CGCI-HTMCP-CC.HTMCP-03-06-02155   
3504  CGCI-HTMCP-CC.HTMCP-03-06-02322   

                             researchsubject_identifier  \
0     [{'system': 'GDC', 'field_name': 'case.case_id...   
1     [{'system': 'GDC', 'field_name': 'case.case_id...   
2     [{'system': 'GDC', 'field_name': 'case.case_id...   
3     [{'system': 'GDC', 'field_name': 'case.case_id...   
4     [{'system': 'GDC', 'field_name': 'case.case_id...   
...                                                 ...   
3500  [{'system': 'GDC', 'field_name': 'case.case_id...   
3501  [{'system': 'GDC', 'field_name': 'case.case_id...   
3502  [{'system': 'GDC', 'field_name': 'case.case_id...   
3503  [{'system': 'GDC', 'field_name': 'case.case_id...   
3504  [{'system': 'GDC', 'field_name': 'case.case_id...   

     member_of_research_project            primary_diagnosis_condition  \
0                     GENIE-NKI    Complex Mixed and Stromal Neoplasms   
1                     GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
2                     GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
3                     GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
4                     GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
...                         ...                                    ...   
3500              CGCI-HTMCP-CC                Squamous Cell Neoplasms   
3501              CGCI-HTMCP-CC                Squamous Cell Neoplasms   
3502              CGCI-HTMCP-CC                Squamous Cell Neoplasms   
3503              CGCI-HTMCP-CC                Squamous Cell Neoplasms   
3504              CGCI-HTMCP-CC                Squamous Cell Neoplasms   

     primary_diagnosis_site              subject_id  
0               Uterus, NOS    GENIE.GENIE-NKI-C0BP  
1              Cervix uteri    GENIE.GENIE-NKI-3OX3  
2              Cervix uteri    GENIE.GENIE-NKI-3GI3  
3              Cervix uteri    GENIE.GENIE-NKI-AGW0  
4              Cervix uteri    GENIE.GENIE-NKI-LVFM  
...                     ...                     ...  
3500           Cervix uteri  CGCI.HTMCP-03-06-02327  
3501           Cervix uteri  CGCI.HTMCP-03-06-02213  
3502           Cervix uteri  CGCI.HTMCP-03-06-02321  
3503           Cervix uteri  CGCI.HTMCP-03-06-02155  
3504           Cervix uteri  CGCI.HTMCP-03-06-02322  

[3505 rows x 6 columns]

In [50]:
subsdf # view the subject dataframe

subject_id  \
0     CGCI.HTMCP-03-06-02393   
1            CPTAC.C3L-01599   
2            CPTAC.C3L-03264   
3            CPTAC.C3N-00847   
4            CPTAC.C3N-01344   
...                      ...   
2704       TCGA.TCGA-E6-A8L9   
2705       TCGA.TCGA-EK-A2R8   
2706       TCGA.TCGA-EX-A1H6   
2707       TCGA.TCGA-FI-A2D4   
2708       TCGA.TCGA-N5-A4RA   

                                     subject_identifier       species     sex  \
0     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
1     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
2     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
3     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
4     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
...                                                 ...           ...     ...   
2704  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
2705  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
2706  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
2707  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
2708  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   

                           race               ethnicity  days_to_birth  \
0     black or african american  not hispanic or latino       -12315.0   
1                         white  not hispanic or latino       -24089.0   
2                         white  not hispanic or latino       -26833.0   
3                         other            not reported       -23757.0   
4                         white            not reported       -29270.0   
...                         ...                     ...            ...   
2704  black or african american  not hispanic or latino       -22333.0   
2705                      white  not hispanic or latino       -17692.0   
2706                      white            not reported       -14214.0   
2707                      white            not reported       -16163.0   
2708                      white      hispanic or latino       -23359.0   

                             subject_associated_project vital_status  \
0                                       [CGCI-HTMCP-CC]         Dead   
1                                 [CPTAC-3, cptac_ucec]        Alive   
2                                 [CPTAC-3, cptac_ucec]        Alive   
3     [CPTAC-3, PDC000125, PDC000126, PDC000226, cpt...        Alive   
4                                 [CPTAC-3, cptac_ucec]         Dead   
...                                                 ...          ...   
2704                             [TCGA-UCEC, tcga_ucec]        Alive   
2705                             [TCGA-CESC, tcga_cesc]        Alive   
2706                             [TCGA-CESC, tcga_cesc]        Alive   
2707                             [TCGA-UCEC, tcga_ucec]         Dead   
2708                               [TCGA-UCS, tcga_ucs]         Dead   

      days_to_death cause_of_death  
0             648.0   Not Reported  
1               NaN           None  
2               NaN           None  
3               NaN           None  
4            1359.0           None  
...             ...            ...  
2704            NaN           None  
2705            NaN           None  
2706            NaN           None  
2707          243.0           None  
2708         1591.0           None  

[2709 rows x 11 columns]

## Merging Results across Endpoints

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Then Julia uses the `subject_id` and `id` fields in each result to merge them together into one big dataset. She also specifies that any columns that are in both tables should be kept and have a suffix added to their name. This will help her to check that her merge worked correctly:

In [51]:
allmetadata = pd.merge(rsdf,
                subsdf,
                left_on="subject_id",
                right_on='subject_id',
                suffixes=("_rs", "_sub"))

allmetadata

researchsubject_id  \
0            GENIE-NKI.GENIE-NKI-C0BP   
1            GENIE-NKI.GENIE-NKI-3OX3   
2            GENIE-NKI.GENIE-NKI-3GI3   
3            GENIE-NKI.GENIE-NKI-AGW0   
4            GENIE-NKI.GENIE-NKI-LVFM   
...                               ...   
3500  CGCI-HTMCP-CC.HTMCP-03-06-02327   
3501  CGCI-HTMCP-CC.HTMCP-03-06-02213   
3502  CGCI-HTMCP-CC.HTMCP-03-06-02321   
3503  CGCI-HTMCP-CC.HTMCP-03-06-02155   
3504  CGCI-HTMCP-CC.HTMCP-03-06-02322   

                             researchsubject_identifier  \
0     [{'system': 'GDC', 'field_name': 'case.case_id...   
1     [{'system': 'GDC', 'field_name': 'case.case_id...   
2     [{'system': 'GDC', 'field_name': 'case.case_id...   
3     [{'system': 'GDC', 'field_name': 'case.case_id...   
4     [{'system': 'GDC', 'field_name': 'case.case_id...   
...                                                 ...   
3500  [{'system': 'GDC', 'field_name': 'case.case_id...   
3501  [{'system': 'GDC', 'field_name': 'case.case_id...   
3502  [{'system': 'GDC', 'field_name': 'case.case_id...   
3503  [{'system': 'GDC', 'field_name': 'case.case_id...   
3504  [{'system': 'GDC', 'field_name': 'case.case_id...   

     member_of_research_project            primary_diagnosis_condition  \
0                     GENIE-NKI    Complex Mixed and Stromal Neoplasms   
1                     GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
2                     GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
3                     GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
4                     GENIE-NKI  Cystic, Mucinous and Serous Neoplasms   
...                         ...                                    ...   
3500              CGCI-HTMCP-CC                Squamous Cell Neoplasms   
3501              CGCI-HTMCP-CC                Squamous Cell Neoplasms   
3502              CGCI-HTMCP-CC                Squamous Cell Neoplasms   
3503              CGCI-HTMCP-CC                Squamous Cell Neoplasms   
3504              CGCI-HTMCP-CC                Squamous Cell Neoplasms   

     primary_diagnosis_site              subject_id  \
0               Uterus, NOS    GENIE.GENIE-NKI-C0BP   
1              Cervix uteri    GENIE.GENIE-NKI-3OX3   
2              Cervix uteri    GENIE.GENIE-NKI-3GI3   
3              Cervix uteri    GENIE.GENIE-NKI-AGW0   
4              Cervix uteri    GENIE.GENIE-NKI-LVFM   
...                     ...                     ...   
3500           Cervix uteri  CGCI.HTMCP-03-06-02327   
3501           Cervix uteri  CGCI.HTMCP-03-06-02213   
3502           Cervix uteri  CGCI.HTMCP-03-06-02321   
3503           Cervix uteri  CGCI.HTMCP-03-06-02155   
3504           Cervix uteri  CGCI.HTMCP-03-06-02322   

                                     subject_identifier       species     sex  \
0     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
1     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
2     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens    male   
3     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
4     [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens    male   
...                                                 ...           ...     ...   
3500  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
3501  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
3502  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
3503  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   
3504  [{'system': 'GDC', 'field_name': 'case.submitt...  Homo sapiens  female   

                           race               ethnicity  days_to_birth  \
0                       Unknown                 Unknown       -20088.0   
1                       Unknown            not reported       -29950.0   
2                       Unknown            not reported       -28489.0  

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
`subject_id` from the research subject results matches `id_sub` from the subjects table. Julia then checks to see that her dataframe is the right size. The number of rows after the merge should be the same as the number of original research subjects:

In [52]:
allmetadata.count()

researchsubject_id             3505
researchsubject_identifier     3505
member_of_research_project     3505
primary_diagnosis_condition    3504
primary_diagnosis_site         3505
subject_id                     3505
subject_identifier             3505
species                        3505
sex                            3461
race                           3378
ethnicity                      3378
days_to_birth                  3078
subject_associated_project     3505
vital_status                   3382
days_to_death                   528
cause_of_death                  147
dtype: int64

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Satisfied with her results, Julia saves the data out to a csv so she can browse it with Excel:

In [53]:
allmetadata.to_csv("allmetadata.csv")

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
   
Julia knows from her subject count summary that there are hundreds of thousands files associated with her subjects, which is likely far more than she needs. To help her decide what files she wants, Julia uses endpoint chaining to get summary information about the files that are assigned to researchsubjects for her search criteria:


In [54]:
NoAdenoData.researchsubject.file.count.run()

Getting results from database

Total execution time: 0
                            min 3.689 sec 3689 ms

total : 364646

data_category 
 count 
 
 
 
 
 DNA Methylation 
 4074 
 
 
 Sequencing Reads 
 9585 
 
 
 Copy Number Variation 
 9098 
 
 
 Simple Nucleotide Variation 
 22200 
 
 
 Peptide Spectral Matches 
 1280 
 
 
 Transcriptome Profiling 
 6210 
 
 
 Imaging 
 297077 
 
 
 Biospecimen 
 5281 
 
 
 Clinical 
 2215 
 
 
 Structural Variation 
 4796 
 
 
 Processed Mass Spectra 
 640 
 
 
 Raw Mass Spectra 
 640 
 
 
 Somatic Structural Variation 
 864 
 
 
 Proteome Profiling 
 686 
 
 
 

 
 
 
 data_type 
 count 
 
 
 
 
 Open Standard 
 1280 
 
 
 Annotated Somatic Mutation 
 10511 
 
 
 Aligned Reads 
 9585 
 
 
 Raw Simple Somatic Mutation 
 6129 
 
 
 Proprietary 
 640 
 
 
 Transcript Fusion 
 4882 
 
 
 Biospecimen Supplement 
 3080 
 
 
 Masked Copy Number Segment 
 1865 
 
 
 Isoform Expression Quantification 
 1436 
 
 
 CT Image Storage 
 163915 
 
 
 MR Image Storage 
 103490 
 
 
 Positron Emission Tomography Image Storage 
 9933 
 
 
 Secondary Capture Image Storage 
 1802 
 
 
 VL Whole Slide Microscopy Image Storage 
 17926 
 
 
 Text 
 640 
 
 
 Masked Intensities 
 2716 
 
 
 Slide Image 
 2201 
 
 
 Clinical Supplement 
 1254 
 
 
 Aggregated Somatic Mutation 
 1419 
 
 
 Raw Intensities 
 1921 
 
 
 Methylation Beta Value 
 1358 
 
 
 miRNA Expression Quantification 
 1436 
 
 
 Masked Somatic Mutation 
 1236 
 
 
 Gene Expression Quantification 
 1669 
 
 
 Copy Number Segment 
 2254 
 
 
 Allele-specific Copy Number Segment 
 930 
 
 
 Splice Junction Quantification 
 1669 
 
 
 Gene Level Copy Number Scores 
 809 
 
 
 Gene Level Copy Number 
 1319 
 
 
 Pathology Report 
 961 
 
 
 Simple Germline Variation 
 1881 
 
 
 Masked Annotated Somatic Mutation 
 1024 
 
 
 Structural Rearrangement 
 778 
 
 
 Protein Expression Quantification 
 686 
 
 
 Digital X-Ray Image Storage - For Presentation 
 2 
 
 
 Computed Radiography Image Storage 
 5 
 
 
 Enhanced SR Storage 
 4 
 
 
 

 
 
 
 file_format 
 count 
 
 
 
 
 mzIdentML 
 640 
 
 
 mzML 
 640 
 
 
 CEL 
 1921 
 
 
 VCF 
 11865 
 
 
 DICOM 
 297077 
 
 
 tsv 
 640 
 
 
 vendor-specific 
 640 
 
 
 MAF 
 8843 
 
 
 BAM 
 9585 
 
 
 IDAT 
 2716 
 
 
 PDF 
 961 
 
 
 SVS 
 2201 
 
 
 TXT 
 9297 
 
 
 BEDPE 
 3053 
 
 
 TSV 
 10237 
 
 
 BCR Biotab 
 76 
 
 
 BCR SSF XML 
 955 
 
 
 BCR XML 
 2093 
 
 
 BCR Auxiliary XML 
 912 
 
 
 BCR PPS XML 
 193 
 
 
 XLSX 
 7 
 
 
 BCR OMF XML 
 71 
 
 
 CDC JSON 
 23 
 
 
 

 
 
 
 file_identifier_system 
 count 
 
 
 
 
 PDC 
 2560 
 
 
 GDC 
 65009 
 
 
 IDC 
 297077

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
    
Julia decides that a good place to start would be with Slide Images. There's only a couple thousand, so she should be able to quickly scan through them over the next few days and see if they will be useful. So she adds one more filter on her search:

In [55]:
JustSlides = Q('data_type = "Slide Image"')
NoadenoJustSlides = NoAdenoData.AND(JustSlides)
NoadenoJustSlides.researchsubject.file.count.run()

Getting results from database

Total execution time: 0
                            min 3.531 sec 3531 ms

total : 2201

data_category 
 count 
 
 
 
 
 Biospecimen 
 2201 
 
 
 

 
 
 
 data_type 
 count 
 
 
 
 
 Slide Image 
 2201 
 
 
 

 
 
 
 file_format 
 count 
 
 
 
 
 SVS 
 2201 
 
 
 

 
 
 
 file_identifier_system 
 count 
 
 
 
 
 GDC 
 2201

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
    
Finally, Julia uses the pagenation function again to get all the slide files, and merges her metadata file with this file information. This way she will be able to review what phenotypes each slide is associated with:

In [56]:
slides = NoadenoJustSlides.researchsubject.file.run()
slidesdf = slides.get_all().to_dataframe()

Getting results from database

Total execution time: 0
                            min 4.006 sec 4006 ms

In [ ]:
slidemetadata = pd.merge(slidesdf, 
                         allmetadata, 
                         left_on=("subject_id","researchsubject_id"),
                         right_on=("subject_id", "researchsubject_id"),
                         suffixes=("_slide", "_all"))
slidemetadata

In [ ]:
slidemetadata.count()

<img src="https://github.com/CancerDataAggregator/readthedocs/blob/main/docs/Tutorials/images/Julia.png?raw=true" align="left"
	width="50" height="50" />
    
Julia saves this dataframe to a csv as well, and now she has all the information she needs to begin work on her project. She can use the `drs_id` column information to directly download the images she is interested in using a DRS resolver, or she can input the DRS IDs at a cloud workspace such as [Terra](https://terra.bio/) or the [Cancer Genomics Cloud](https://www.cancergenomicscloud.org/) to view the images online. In either case, she has all the metadata she needs to get started, and can save this notebook of her work in case she'd like to come back and modify her search.

In [59]:
slidemetadata.to_csv("slidemetadata.csv")